In [1]:
import embed_anything
from embed_anything import EmbedData
from tqdm.autonotebook import tqdm
from pinecone import Pinecone, ServerlessSpec
import numpy as np
import os
from pinecone import PineconeApiException
import uuid

C:\Users\arbal\AppData\Local\Temp\ipykernel_27040\3276458500.py:3: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm


In [2]:
audio_files = ["examples/samples_hp0.wav", "examples/samples_gb0.wav"]

In [3]:
embeddings: list[list[EmbedData]] = []

In [4]:
for file in audio_files:
    embedding = embed_anything.embed_file(file, "Whisper-Jina")
    embeddings.append(embedding)

In [96]:
pc = Pinecone(api_key=os.environ.get("PINECONE_API_KEY"))
pc.delete_index("search-in-audio")
try:
   index =  pc.create_index(
        name="search-in-audio",
        dimension=768, # Replace with your model dimensions
        metric="cosine", # Replace with your model metric
        spec=ServerlessSpec(
            cloud="aws",
            region="us-east-1"
        ) 
    )
   index = pc.Index('search-in-audio')
except(PineconeApiException) as e:
    index = pc.Index('search-in-audio')
    if e.status == 409:
        print("Index already exists")
    
    else: print(e)

In [97]:
## convert embeddings which is of the form EmbedData : text, embedding, metadata to the form required by pinecone which is id, values, metadata
import re
def convert_to_pinecone_format(embeddings: list[list[EmbedData]]):
    data = []
    for i, embedding in enumerate(embeddings):
        for j, emb in enumerate(embedding):
            data.append({"id": str(uuid.uuid4()), "values": emb.embedding, "metadata": {"text": emb.text, "start": emb.metadata["start"], "end": emb.metadata["end"], "file": re.split(r'/|\\',emb.metadata["file_name"])[-1]}})
    return data

In [98]:
data = convert_to_pinecone_format(embeddings)
index.upsert(data)

{'upserted_count': 15}

In [99]:
query = embed_anything.embed_query(['united states'], "Jina")[0]

In [100]:
result = index.query(vector=query.embedding, top_k=5, include_metadata=True,)


In [101]:
for res in result.matches:
    print(res.metadata)

{'end': '120', 'file': 'samples_gb0.wav', 'start': '90', 'text': " Young democracy from Georgia and Ukraine to Afghanistan and Iraq can look to the United States for proof that self-government can endure and nations that still live under tyranny and oppression can find hope and inspiration in our commitment to liberty. For more than two centuries, Americans have demonstrated the ability of free people to choose their own leaders. Our nation has flourished because of its commitment to trusting the wisdom of our citizenry. In this year's election, we will see this tradition continue and we will be reminded once again"}
{'end': '60', 'file': 'samples_gb0.wav', 'start': '30', 'text': ' The United States was founded on the belief that all men are created equal. Every election day, millions of Americans of all races, religions and backgrounds step into voting booths throughout the nation, whether they are richer, poor, older, young. Each of them has an equal share in choosing the path that o

In [104]:
import gradio as gr
files = ["samples_hp0.wav", "samples_gb0.wav"]
def search(query, audio):

    results = []
    query = embed_anything.embed_query([query], "Jina")[0]

    if re.split(r'/|\\',audio)[-1] not in files:
            print(file, re.split(r'/|\\',audio)[-1])
            embeddings = embed_anything.embed_file(audio, "Whisper-Jina")
            embeddings = convert_to_pinecone_format([embeddings])
            index.upsert(embeddings)

    files.append(re.split(r'/|\\',audio)[-1])


    result = index.query(vector=query.embedding, top_k=5, include_metadata=True,)
    for res in result.matches:
        results.append(res.metadata)
    
    formatted_results = []
    for result in results:
        display_text = f'''
        
        `File: {result['file']}`
        
        `Start: {result['start']}`
        
        `End: {result['end']}`
        
        Text: {result['text']}'''  
        formatted_results.append(display_text)

    return formatted_results[0], results[0]['file'], formatted_results[1],  results[1]['file'], formatted_results[2], results[2]['file']

demo = gr.Interface(
    fn=search,
    inputs=["text", gr.Audio(label='Audio', type = 'filepath')],
    outputs=[
        
        gr.Markdown(label="Text"), gr.Audio(label="Audio", type="filepath"),
        gr.Markdown(label="Text"), gr.Audio(label="Audio", type="filepath"),
        gr.Markdown(label="Text"), gr.Audio(label="Audio", type="filepath")
    ],
    examples=[["screwdriver", "examples/samples_hp0.wav"], ["united states", "examples/samples_gb0.wav"], ["united states", "examples/samples_hp0.wav"]],
)
demo.launch()

Running on local URL:  http://127.0.0.1:7899

To create a public link, set `share=True` in `launch()`.


In [89]:
audio = "C:/Users/arbal/AppData/Local/Temp/gradio/c0490405f0fef485a043991c6a9d6b83f006db51/samples_hp0.wav"
"samples_hp0.wav" not in audio

False

In [94]:
if "samples_hp0.wav" not in "C:\Users\arbal\AppData\Local\Temp\gradio\c0490405f0fef485a043991c6a9d6b83f006db51\samples_hp0.wav"

SyntaxError: (unicode error) 'unicodeescape' codec can't decode bytes in position 2-3: truncated \UXXXXXXXX escape (1955374795.py, line 1)

In [93]:
re.split(r'/|\\',audio)[-1]

'samples_hp0.wav'